In [1]:
import os
import numpy as np
import pandas as pd
import datetime

In [2]:
from openpyxl import load_workbook

In [3]:
path_to_sheet = r"C:\Users\a.jurcenko\Desktop\Ralf Fischer\Stempelzeiten Erding Oktober 2023.xlsx"

In [4]:
wb = load_workbook(filename=path_to_sheet)
ws = wb.active
xl = pd.ExcelFile(path_to_sheet)
nrows = xl.book.active.max_row
print(nrows)

816


In [5]:
def parse_time_string(time_string):
    come = time_string.endswith('K')
    time_string = time_string.replace('*', '').strip()[:5]
    return time_string, come

In [16]:
def parse_info(first_row, last_row, info):
    df_times = pd.read_excel(path_to_sheet, skiprows=first_row, skipfooter=nrows-last_row-1)
    user = info.split(':')
    user_id = user[1].strip()[:4]
    user_surname, user_name = user[0].split(',')
    user_name = user_name.split('-')[0].strip()
    user = user_surname[:8]
    # print(user_name)
    times = list()
    for index, row in df_times.iterrows():
        date = row['Datum']
        direction = 'Hinaus'
        for r in (row['Buchungen'], row['Unnamed: 5']):
            if str(r) != 'nan':
                if r.find('\n') > -1:
                    for s in r.split('\n'):
                        tm, come = parse_time_string(s)
                        if come:
                            direction = 'Herein'
                        else:
                            direction = 'Hinaus'
                        times.append({'Benutzername': user, 'Vorname': user_name, 'Nachname': user_surname, 'Abteilung': 'Erding', \
                          'Person': user_id,  'Wann': date + ' ' + tm + ':00', 'Gerät': 'Erding', 'Hinein/Hinaus': direction, 'Überprüfung': 'RFID'})
                            
                else:
                    tm, come = parse_time_string(r)
                    if come:
                        direction = 'Herein'
                    else:
                            direction = 'Hinaus'
                        
                    times.append({'Benutzername': user, 'Vorname': user_name, 'Nachname': user_surname, 'Abteilung': 'Erding', \
                                  'Person': user_id,  'Wann': date + ' ' + tm + ':00' , 'Gerät': 'Erding', 'Hinein/Hinaus': direction, 'Überprüfung': 'RFID'})
    # print(times)
    return times


In [17]:
# info = "Fischer, Achraf - P1: 1508 - Ausweis: 159 - VWG: Erding"
# first_cell = 273
# last_cell = 305
# time_table = parse_info(first_cell, last_cell, info)
# print(time_table)

In [18]:
rows = list(ws.rows)

all_df = list()
for row in rows:
    for cell in row: # Zellen
        if cell.value is None or type(cell.value) == float:
            continue
        elif cell.value.find('Ausweis') > -1:
            first_cell = cell.row
            info = cell.value
        elif cell.value.find('gesamt') > -1:
            last_cell = cell.row
            time_table = parse_info(first_cell, last_cell, info)
            if len(time_table) > 0:
                all_df.append(pd.DataFrame(time_table))

In [19]:
df_cum = pd.concat(all_df)

In [20]:
#df_cum = pd.DataFrame(time_table)
df_cum.groupby(['Benutzername', 'Vorname', 'Nachname', 'Abteilung', 'Person', 'Wann', 'Gerät', 'Hinein/Hinaus', 'Überprüfung']).all()

Empty DataFrame
Columns: []
Index: [(Braun, Tobias, Braun, Erding, 1515, 02.10.2023 05:45:00, Erding, Herein, RFID), (Braun, Tobias, Braun, Erding, 1515, 02.10.2023 07:17:00, Erding, Hinaus, RFID), (Braun, Tobias, Braun, Erding, 1515, 04.10.2023 09:42:00, Erding, Herein, RFID), (Braun, Tobias, Braun, Erding, 1515, 04.10.2023 09:43:00, Erding, Hinaus, RFID), (Braun, Tobias, Braun, Erding, 1515, 10.10.2023 06:00:00, Erding, Herein, RFID), (Braun, Tobias, Braun, Erding, 1515, 10.10.2023 09:00:00, Erding, Hinaus, RFID), (Braun, Tobias, Braun, Erding, 1515, 26.10.2023 05:39:00, Erding, Herein, RFID), (Braun, Tobias, Braun, Erding, 1515, 26.10.2023 08:37:00, Erding, Hinaus, RFID), (Broushak, Farnaz, Broushaky, Erding, 1478, 04.10.2023 09:41:00, Erding, Herein, RFID), (Broushak, Farnaz, Broushaky, Erding, 1478, 04.10.2023 09:41:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 09.10.2023 06:00:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 09.10.2023 10:00:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 09.10.2023 10:30:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 09.10.2023 15:00:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 10.10.2023 05:58:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 10.10.2023 10:10:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 10.10.2023 10:39:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 10.10.2023 15:07:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 11.10.2023 07:56:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 11.10.2023 11:45:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 11.10.2023 12:14:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 11.10.2023 16:06:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 12.10.2023 07:51:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 12.10.2023 16:22:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 13.10.2023 07:59:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 13.10.2023 12:20:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 13.10.2023 12:48:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 13.10.2023 15:50:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 16.10.2023 06:01:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 16.10.2023 10:23:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 16.10.2023 10:52:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 16.10.2023 15:15:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 17.10.2023 06:54:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 17.10.2023 11:09:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 17.10.2023 11:37:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 17.10.2023 17:39:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 18.10.2023 06:56:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 18.10.2023 10:45:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 18.10.2023 11:11:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 18.10.2023 16:54:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 19.10.2023 06:57:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 19.10.2023 10:40:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 19.10.2023 11:07:00, Erding, Herein, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453, 19.10.2023 15:58:00, Erding, Hinaus, RFID), (Czehmeis, Zoltan, Czehmeiszter, Erding, 1453,

In [21]:
writer = pd.ExcelWriter(
    r"C:\Users\a.jurcenko\Desktop\Ralf Fischer\Stempelzeiten Erding Oktober 2023 erweitert.xlsx",
    engine="xlsxwriter",
    datetime_format="hh:mm:ss",
)

In [22]:
df_cum.to_excel(writer, index=False)

In [23]:
writer.close()